In [33]:
df = pd.DataFrame(columns=('Stock', 'Corr'))
df.loc[0] = ['GOOG', .88]
df.loc[1] = ['GOOG2', .38]
df.loc[2] = ['APPL', .11]
df.loc[3] = ['GOOG3', .77]

df.loc[1, 'Corr'] # gives value for index of 1 and column Corr

df = df.set_index('Stock') # set index to date 

df.loc['GOOG3', 'Corr'] #look up by index name

new_corr = .888
indiv_stock = 'GOOG3'

if new_corr > df.loc[indiv_stock, 'Corr']:
    df.loc[indiv_stock, 'Corr'] = new_corr #set column in df to new number
    
print( df.loc[indiv_stock, 'Corr'] ) #proof




#data_ema = data_ema.set_index('Stock') # set index to date

#data_ema

0.888


In [78]:
# used to work...now plot won't show up
%matplotlib notebook

from datetime import datetime, timedelta
import quandl
import math
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import style
style.use('fivethirtyeight')

api_key = 'kgMN5tuNUwb7-F29s6xp' 

def corr_data(stock_num):
    ##----------TRAINING DATA
    main_df = pd.DataFrame()

    file = 'gainers_2017_03_04_training_4_perc_jumps.csv'
    df = pd.read_csv('data/training_data/'+file)
    df = df.set_index('Index').T

    for column in df:    
        main_df[column] = (df[column] - df[column].iloc[0]) / df[column].iloc[0] * 100

    #CURRENT
    df2= main_df
    df3 = pd.DataFrame()
    main_df3 = pd.DataFrame()
    df_corr_results = pd.DataFrame()
    main_df_corr_results = pd.DataFrame()
    main_df_corr_results_temp = pd.DataFrame()
    main_plot = pd.DataFrame()

    #---------THE FILES TO ANALYZE
    #df3 = pd.read_csv('gainers-loser/daily_exports/file 4-2017.csv')
    train1 = pd.read_csv('data/daily_exports/nav_2017-06-02.csv')
    #train1 = pd.read_csv('data/daily_exports/gainers_2017-05-24-25-26.csv')
    train1 = train1.set_index('Index').T

    #-------main testing data
    #stock_corr = pd.DataFrame(columns=('Stock', 'Corr'))
    row_corr_inc = 0
    
    x_test = 0
    y_test = 30
    stop_loop = 0
    while x_test <= 0: #default is y_test, but use stop_loop for testing. This was to move the stocks up and down
        df3 = train1 # clear testing data
        
        for column in df3:    
            main_df3[column] = ((df3[column] - df3[column].iloc[0]) / df3[column].iloc[0] * 100) - x_test

        #num_days = 40 # used in future only
        analyze_stock_text = df3.columns.values[stock_num]
        x1 = main_df3[analyze_stock_text] # convert selected stock to series so you can coorilate

        x1.index = x1.index.map(int) # turn index into integers so they can be manipulated

        x = 0
        for num in x1:
            if math.isnan(x1[x]) == True:
                x1.pop(x)
            x+=1

        ##start brute force here!!!

        x = 0
        y = len(df3) - len(x1)
        main_df_corr_results = pd.DataFrame()
        main_df_corr_results_temp = pd.DataFrame()
        
        #setup variables to use in list of Stock/Corr results
        row_corr_count = 0
        stock_corr = {} # set as a dictionary

        while x <= 5: #set to 5 for testing and y to for normal runs

            range_x = y - x
            range_y = len(x1)+y - x

            x1.index = x1.index.map(int) # turn index into integers so they can be manipulated
            #x1.index = range(range_x,first_looprange_y) # moves stock on x axis
            x1.index = range(range_x,range_y) # moves stock on x axis
            x1.index = x1.index.map(str) # turn back into string so it can be plotted

            analyze_plots = pd.DataFrame(data=main_df3[analyze_stock_text]) #convert into df to use to plot

            # correlate selected stock to all test data stocks
            df_corr_results = df2.corrwith(x1)
            main_df_corr_results_temp = df_corr_results.sort_values(ascending=False)
            main_df_corr_results = pd.DataFrame({'Stock':main_df_corr_results_temp.index, 'Corr':main_df_corr_results_temp.values}) #turns series into a dataframe

            d = datetime.today() - timedelta(days=1) # today's day  minus one for plot display

            count_set = 0
            for index, row in main_df_corr_results.iterrows(): # loop each value of main_df_corr...

                if row['Corr'] >= .80:
                    
                    count_set+=1
                    
                    if row['Stock'] not in stock_corr:
                        stock_corr[ row['Stock'] ] = row['Corr']
                    else:
                        if row['Corr'] > stock_corr[ row['Stock'] ]:
                            stock_corr[ row['Stock'] ] =  new_corr #set column in df to new number
        
            print(str(count_set)+' stocks found...')

                #stock_corr.loc[row_corr_count] = [ '2017-04-20|NNI' , .9999]      #0.886832
                    
            x+=1 # while x >= y
            
        x_test += 10
    
    print(stock_corr)
    
    df_stock_corr = pd.DataFrame()
    df_stock_corr['Stock'] = stock_corr.keys()
    df_stock_corr['Corr'] = stock_corr.values()
    
    for line in df_stock_corr:
        first_loop = 1

        # adjust plot titles
        #bench
        benchmark_stock_text = Stock
        bench_date, bench_stock = benchmark_stock_text.split('|')
        date_object = datetime.strptime(bench_date, '%Y-%m-%d')
        bench_date = date_object.strftime('%d-%b-%y')
        title_benchmark_stock_text = bench_stock+'|'+bench_date

        #other
        analy_date, analy_stock = analyze_stock_text.split('|')
        date_object = datetime.strptime(analy_date, '%Y-%m-%d')
        analy_date = date_object.strftime('%d-%b-%y')
        title_analyze_stock_text = analy_stock+'|'+analy_date



        #show correlated values
        print('TEST: '+str(analyze_stock_text))
        print (Corr_perc, Stock)
        print()

        #---------pick a benchmark
        print('Benchmark: '+str(benchmark_stock_text))
        benchmark_plots = pd.DataFrame(data=df2[benchmark_stock_text]) #loopup benchmark data using TEXT
        #---------pick a benchmark

        # plot data
        main_plot['Bench: '+title_benchmark_stock_text] = benchmark_plots[benchmark_stock_text]
        main_plot[''+title_analyze_stock_text] = analyze_plots[analyze_stock_text]
        #main_plot['Future:'+analyze_stock_text] = analyze_plots_future # uncomment for future
        main_plot.plot()
        corr = int(Corr_perc * 100)
        plt.title('Corr='+ str(corr)+'%')
        plt.xlabel('['+str(stock_num)+'] '+file+'\nLast Stock Update: '+d.strftime('%Y-%m-%d'), fontsize=10)
        plt.tight_layout() # make room for lables
        #plt.show() # you can also use plt.show()

        del main_plot['Bench: '+title_benchmark_stock_text] # delete line from PLOT
        del main_plot[title_analyze_stock_text]
        #del main_plot['Future:'+analyze_stock_text] # uncomment for future  
    
    
    
    
    
    
    
    
    
    
    
    
    print('done')
    
corr_data(0)

10 stocks found...
6 stocks found...
5 stocks found...
7 stocks found...
6 stocks found...
4 stocks found...
{'2017-04-07|BNED': 0.8852653692768757, '2017-03-22|AXR': 0.888, '2017-04-24|EROS': 0.888, '2017-03-16|CPAC': 0.846008145032336, '2017-03-30|CIA': 0.8396654898552731, '2017-03-23|SXC': 0.8190403905230957, '2017-04-10|AMBR': 0.888, '2017-03-29|LXU': 0.8117988866392774, '2017-04-26|SID': 0.8100771143191907, '2017-04-20|CLF': 0.8057713051925193, '2017-04-27|WNS': 0.8709310457155777, '2017-04-05|ALR': 0.8208180128753751, '2017-04-18|CSLT': 0.8315944722821819, '2017-04-18|CAB': 0.888, '2017-04-18|MC': 0.8044065273498524, '2017-04-10|KNX': 0.888, '2017-04-10|RRTS': 0.8014935112782743, '2017-04-10|SWFT': 0.888, '2017-04-06|TEX': 0.8112016440480988}
              Stock      Corr
0   2017-04-07|BNED  0.885265
1    2017-03-22|AXR  0.888000
2   2017-04-24|EROS  0.888000
3   2017-03-16|CPAC  0.846008
4    2017-03-30|CIA  0.839665
5    2017-03-23|SXC  0.819040
6   2017-04-10|AMBR  0.888000
7

In [ ]:
                for line in stock_corr:

                    first_loop = 1

                    # adjust plot titles
                    #bench
                    benchmark_stock_text = Stock
                    bench_date, bench_stock = benchmark_stock_text.split('|')
                    date_object = datetime.strptime(bench_date, '%Y-%m-%d')
                    bench_date = date_object.strftime('%d-%b-%y')
                    title_benchmark_stock_text = bench_stock+'|'+bench_date

                    #other
                    analy_date, analy_stock = analyze_stock_text.split('|')
                    date_object = datetime.strptime(analy_date, '%Y-%m-%d')
                    analy_date = date_object.strftime('%d-%b-%y')
                    title_analyze_stock_text = analy_stock+'|'+analy_date



                    #show correlated values
                    print('TEST: '+str(analyze_stock_text))
                    print (Corr_perc, Stock)
                    print()

                    #---------pick a benchmark
                    print('Benchmark: '+str(benchmark_stock_text))
                    benchmark_plots = pd.DataFrame(data=df2[benchmark_stock_text]) #loopup benchmark data using TEXT
                    #---------pick a benchmark

                    # plot data
                    main_plot['Bench: '+title_benchmark_stock_text] = benchmark_plots[benchmark_stock_text]
                    main_plot[''+title_analyze_stock_text] = analyze_plots[analyze_stock_text]
                    #main_plot['Future:'+analyze_stock_text] = analyze_plots_future # uncomment for future
                    main_plot.plot()
                    corr = int(Corr_perc * 100)
                    plt.title('Corr='+ str(corr)+'%')
                    plt.xlabel('['+str(stock_num)+'] '+file+'\nLast Stock Update: '+d.strftime('%Y-%m-%d'), fontsize=10)
                    plt.tight_layout() # make room for lables
                    #plt.show() # you can also use plt.show()

                    del main_plot['Bench: '+title_benchmark_stock_text] # delete line from PLOT
                    del main_plot[title_analyze_stock_text]
                    #del main_plot['Future:'+analyze_stock_text] # uncomment for future     